# Generalized Vehicle Routing Problem

## Parser

In [1]:
#!/usr/bin/env python3
# -*- coding: utf-8 -*-
"""
Created on Thu Sep 12 22:46:37 2019

@author: andreamourelo
"""

from IPython.display import display, Markdown, Latex
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import matplotlib
import warnings
warnings.filterwarnings('ignore')
import csv
import numpy as np
import sys, getopt
import math

#def gvrp(filename, seed):
#print('Start processing file :', instance)

filename = 'GVRP/A-n32-k5-C11-V2.gvrp'
instance = (filename[:-5])
delimiter = ' '
#print(instance)

# No final, vamos ter:
# nodes = [node1, node2, ..., nodenNodes] = [[x_pos_node1, y_pos_node1, group_node_1], ....]
# com group_node entre [1, nGroups]

# e demands = [demand_group_1, demand_group_2, ..., demand_group_nGroups]
with open(filename,'r') as file:
    csv_reader = csv.reader(file,
                           delimiter = delimiter)
    line_count = 0
    node_count = 0
    group_count = 0
    nNodes, nGroups, nVehicles, capacity = 0,0,0,0
    for row in csv_reader:
        if line_count == 2 :  # DIMENSION : nNodes
            nNodes = int(row[2])
            nodes = np.zeros((nNodes,3), dtype=np.int)
        elif line_count == 3 : # VEHICLES : nVehicles
            nVehicles = int(row[2])
        elif line_count == 4 : # GVRP_SETS : nGroups
            nGroups = int(row[2])
            groups = [[0]] # Para guardar uma lista com os grupos
            demands = np.zeros((nGroups), dtype=np.int)
        elif line_count == 5 :
            capacity = int(row[2]) # CAPACITY : capacity
        elif line_count >= 8 and line_count <= 8 + nNodes +  - 1: # Informacoes sobre as posicoes dos nos => num x_pos y_pos
            nodes[node_count] = [int(row[1]),int(row[2]), 0] # Ainda nao temos info sobre o grupo do nó, no depot vai ter grupo 0 
            node_count += 1
        elif line_count >= 8 + nNodes + 1 and line_count <= 8 + nNodes + nGroups: # Informacoes sobre os grupos => num_grupo elem elem ... elem -1
            nNodesInGroup = len(row)
            group = []
            for numNode in range(1,nNodesInGroup - 1 ): # Para evitar o "-1" que mostra quando pular linha
                nodeOfGroup = int(row[numNode]) - 1
                nodes[nodeOfGroup][2]  = group_count + 1
                group.append(nodeOfGroup)
            group_count += 1
            groups.append(group)
            if group_count == nGroups:
                group_count = 0  # Reseteando no final para usar na leitura seguinte
        elif line_count >= 8 + nNodes + nGroups + 2 and line_count <= 8 + nNodes + 2*(nGroups + 1) - 1:
            demands[group_count] = int(row[1])
            group_count += 1
        line_count += 1

print(nNodes, nVehicles, nGroups, capacity)
print(nodes)
print(groups)
print(demands)  
    
    #print('Ending processing file :', instance)
    
#if __name__ == "__main__":
#    gvrp(sys.argv[1], seed) # Implement seed


32 2 11 100
[[82 76  0]
 [96 44  2]
 [50  5  6]
 [49  8  6]
 [13  7  1]
 [29 89  9]
 [58 30 10]
 [84 39 11]
 [14 24  1]
 [ 2 39  8]
 [ 3 82  3]
 [ 5 10  1]
 [98 52  2]
 [84 25 11]
 [61 59  5]
 [ 1 65  7]
 [88 51  2]
 [91  2  4]
 [19 32  8]
 [93  3  4]
 [50 93  9]
 [98 14  4]
 [ 5 42  8]
 [42  9  6]
 [61 62  5]
 [ 9 97  3]
 [80 55  2]
 [57 69  5]
 [23 15  1]
 [20 70  7]
 [85 60  2]
 [98  5  4]]
[[0], [11, 4, 8, 28], [12, 1, 16, 26, 30], [25, 10], [17, 19, 21, 31], [27, 14, 24], [3, 2, 23], [15, 29], [9, 18, 22], [20, 5], [6], [13, 7]]
[13 14 16 16 15 11 12  7  7 12 16]


## Auxiliary functions

In [23]:
import random

# Função usada para o set up da seed a cada função, pois se não não funcionava
def set_seed():
    # Set a seed value: 
    seed_value = 1001004  
    # 1. Set PYTHONHASHSEED environment variable at a fixed value: 
    import os
    os.environ['PYTHONHASHSEED']=str(seed_value) 
    # 2. Set python built-in pseudo-random generator at a fixed value:
    random.seed(seed_value) 
    # 3. Set numpy pseudo-random generator at a fixed value:
    np.random.seed(seed_value) 

def createInitialSolutionRandomly(nVehicles, nGroups): # Doesnt YET check if the solution is FEASIBLE (capacities!!)
    # For now, creates list of np.arrays with each np.array being the route followed by a vehicle
    set_seed()
    routes = []
    for vehicle in range(nVehicles): # Preparing routes = [[],[],....,[]]
        routes.append([0])
    for group in range(nGroups): # Randomly assigning a vehicle for each group
        groupVehicle = random.randint(0,nVehicles - 1)
        routes[groupVehicle].append(group)
    for vehicle in range(nVehicles): # Preparing routes = [[],[],....,[]]
        routes.append(0)
    return routes
    #return [np.array(route) for route in routes]

def createInitialSolutionByBruteForce(nVehicles, nGroups, capacity, demands):
    routes = []
    for vehicle in range(nVehicles): # Preparing routes = [[],[],....,[]]
        routes.append([0]) # Todas começam em 0
    vehicleToFill = 0
    capacityFilled = 0
    capacities = []
    for group in range(1,nGroups):
        groupDemand = demands[group]
        space = capacity - capacityFilled
        if groupDemand < space:
            routes[vehicleToFill].append(group)
            capacityFilled += groupDemand
        else:
            capacities.append(capacityFilled)
            vehicleToFill += 1
            capacityFilled = 0
            routes[vehicleToFill].append(group)
            capacityFilled += groupDemand
    capacities.append(capacityFilled)
    #print('capacities : ',capacities)
    for vehicle in range(nVehicles): # Preparing routes = [[],[],....,[]]
        routes[vehicle].append(0) # Todas começam em 0
    return routes, capacities
    #return [np.array(route) for route in routes]
        
def localSearch(routes, distances): # distances is a matrix with total distances for each vehicle
    routes_final = routes
    min_distances = distances
    # 2-opt em todas as rotas
    for num_route in range(len(routes_final)):
        print("hola")
        route_iteration = routes_final[num_route]
        iterations = 0
        min_distance = min_distances[num_route]
        print(route_iteration)
        while(iterations < len(route_iteration) - 3): # nao contando os depots
            route_2opt_numbers = [i for i in range(len(route_iteration))][1:-1] # para nao tirar o depot
            print("iterations : ", iterations)
            num_group1 = random.choice(route_2opt_numbers)
            print(num_group1)
            #del route_2opt_numbers[num_group1] # removes by index
            route_2opt_numbers.remove(num_group1)
            print(route_2opt_numbers)
            num_group2 = random.choice(route_2opt_numbers)
            group1, group2 = route_iteration[num_group1], route_iteration[num_group2]
            #group1 = random.choice(route_iteration)
            #route_iteration.remove(group1) # removes by first value encountered equal to "group1"
            #group2 = random.choice(route_iteration)
            print(route_iteration, group1,group2)
            iterations += 1
            # 2-opt => the new solution will always be feasible because the capacities will be the same
            new_route = twoOptIntra(routes_final[num_route], num_group1, num_group2)
            new_distance = calculateDistanceAfter2Opt(new_route, group1, group2)
            if new_distance < min_distance:
                print("saindo")
                route_iteration = new_route
                min_distance = new_distance
                iterations = 0
                routes_final[num_route] = route_iteration
                min_distances[num_route] = min_distance
    # Fazemos cross   
    print("cross")
    iterations = 0
    routes_cross = routes_final
    distances_cross = min_distances
    #routes_cross_numbers = list(range(len(routes_cross)))
    while (iterations < len(routes_cross)):
        print(routes_cross)
        routes_cross_numbers = [i for i in range(len(routes_cross))]
        num_route1 = random.choice(routes_cross_numbers)
        #del routes_cross_numbers[num_route1] # removes by index
        routes_cross_numbers.remove(num_route1)
        num_route2 = random.choice(routes_cross_numbers)
        route1, route2 = routes_cross[num_route1], routes_cross[num_route2]
        min_length = min(len(route1),len(route2))
        nums_groups = [i for i in range(min_length)]
        group1 = random.choice(nums_groups)
        #del nums_groups[group1]
        nums_groups.remove(group1)
        group2 = random.choice(nums_groups)
        new_route1, new_route2 = cross(route1,route2,group1,group2)
        iterations += 0
        # We need to check if the new_routes are feasible
        if isFeasible(new_route1) and isFeasible(new_route2):
            new_distance1, new_distance2 = calculateDistanceAfterCross(new_route1, new_route2, group1, group2)
            if new_distance1 + new_distance2 < min_distances[num_route1] + min_distances[num_route2]:
                routes_final[num_route1] = new_route1
                routes_final[num_route2] = new_route2
                min_distances[num_route1] = new_distance1
                min_distances[num_route2] = new_distance2
                iterations = len(routes_cross)        
    return routes_final

def calculateDistanceAfter2Opt(new_route, group1, group2):
    new_distance = 0
    return new_distance
    
def calculateDistanceAfterCross(new_route1, new_route2, group1, group2):
    new_distance1, new_distance2 = 0, 0
    return new_distance1, new_distance2

def calculateDistancesForRoutes(routes, distances):
    distancesPerVehicle = np.zeros(len(routes))
    for vehicle in range(len(routes)):
        p = FloydWarshall(distances, routes[vehicle])
        totalDistanceOfVehicle = p[0][0]
        distancesPerVehicle[vehicle] = totalDistanceOfVehicle
    return distancesPerVehicle

def calculateDistance(routesWithNodes, distances):
    # We need nodes that are visited
    distance = 0
    for route in routesWithNodes:
        for node in range(len(route) - 1): # Evitating last one 
            #distance += distances[route[node]][route[node + 1]]
            distance = 0
    return distance

def perturbate(routes):
    return routes

def twoOptIntra(route, group1, group2):
    # Will remove and replace 2 edges in the route
    # example: with route = [1,2,3,4,5,6,7,8], twoOptIntra(route, 2, 5) returns [1 2 3 6 5 4 7 8]
    print(route, group1,group2)
    temporary = route[group1 + 1 : group2]
    new_route = route[:group1 + 1] + [route[group2]] + temporary[::-1] + route[group2 + 1 : ]
    return new_route

def twoOptInter(route1, route2, group):
    # Will remove and replace 2 consecutive edges in two different routes
    # example : with route1 = [1,2,3,4,5,6,7,8] and route2 = [9,10,11,12]
    # twoOptInter(route1, route2, 1)
    # will give (array([ 1,  2, 11, 12]), array([ 9, 10,  3,  4,  5,  6,  7,  8]))
    new_route1 = route1[:group + 1] + route2[group + 1 :]
    new_route2 = route2[:group + 1] + route1[group + 1 :]
    return new_route1, new_route2

def cross(route1, route2, group1, group2):
    # Will exchange 2 sequences of visits
    # example : with route1 = [1,2,3,4,5,6,7,8] and route2 = [9,10,11,12]
    # cross(route1, route2, 1, 3)
    # will return ([1, 2, 11, 12, 5, 6, 7, 8], [9, 10, 3, 4])    
    route1_temporary, route2_temporary = twoOptInter(route1, route2, group1)
    route1_final, route2_final = twoOptInter(route1_temporary, route2_temporary, group2)
    return route1_final, route2_final

def isFeasible(route):
    demandOfRoute = 0
    for group in route:
        demandOfRoute += demands[group]
        if demandOfRoute > capacity :
            return False
    return True

# def calculateDistanceAfterChange(route, ...??):



In [3]:
distances = np.full((nNodes,nNodes), 100000000000)

for node in range(0,nNodes):
    for second_node in range(node+1,nNodes):
        if nodes[node][2] != nodes[second_node][2]: # Nao queremos arestas entre os nós de um mesmo grupo
            x1, x2 = nodes[node][0], nodes[second_node][0]
            y1, y2 = nodes[node][1], nodes[second_node][1]
            distance2 = (x2 - x1)**2 + (y2 - y1)**2
            distances[node][second_node] = math.sqrt(distance2)
            distances[second_node][node] = math.sqrt(distance2)
            
print(pd.DataFrame(distances).head(5))

             0             1             2             3             4   5   \
0  100000000000            34            77            75            97  54   
1            34  100000000000            60            59            90  80   
2            77            60  100000000000  100000000000            37  86   
3            75            59  100000000000  100000000000            36  83   
4            97            90            37            36  100000000000  83   

   6   7             8   9  ...  22            23  24   25            26  27  \
0  51  37            85  88 ...  84            78  25   75            21  25   
1  40  13            84  94 ...  91            64  39  101  100000000000  46   
2  26  48            40  58 ...  58  100000000000  58  100            58  64   
3  23  46            38  56 ...  55  100000000000  55   97            56  61   
4  50  77  100000000000  33 ...  35            29  73   90            82  76   

             28  29            30  31  
0   

In [4]:
def novasDistancias(distances, route, nNodes, groups):
    nos = [0]
    novasDistancias = np.full((nNodes,nNodes), 100000000000) # copiamos matriz de distancias
    for i in range(len(route) - 1): # e mudamos valores para infinito quando nao sao do grupo
        group = route[i]
        next_group = route[i+1]
        nos_grupo = groups[next_group]
        nos += nos_grupo
        grupo1 = groups[group]
        grupo2 = groups[next_group]
        for node in grupo1:
            for i in range(nNodes):
                if i in grupo2:
                    novasDistancias[node][i] = distances[node][i]
                    #novasDistancias[i][node] = distances[node][i]
    #print(pd.DataFrame(novasDistancias))
    return novasDistancias
        
#novasDistancias = novasDistancias(distances, [0,2,11,6], 32, groups)

In [5]:
def FloydWarshall(distances, route):
    distances = novasDistancias(distances, route, nNodes, groups)
    parent = []
    v = len(distances)
    # path reconstruction matrix
    p = np.zeros(distances.shape)
    for i in range(0,v):
        for j in range(0,v):
            p[i,j] = distances[i,j]

    # initialize to infinity
    for i in range (0, v):
        parent.append([])
        for j in range (0, v):
            parent[i].append(0)

    # initialize the path matrix
    for i in range (0,v):
        for j in range (0,v):
            if distances[i][j] == float("inf"):
                parent[i][j] = 0
            else:
                parent[i][j] = i

    changed = 0
    for k in range(0,v):
        for i in range(0,v):
            for j in range(0,v):
                if p[i,j] > p[i,k] + p[k,j]:
                    p[i,j] = p[i,k] + p[k,j]
                    parent[i][j] = parent[k][j]
                    changed +=1
    print("\n")
    #print("\n\n\n")
    
    # display shortest paths 

    # recursive function to obtain the path as a string
    def obtainPath(i, j):
        if distances[i][j] == float("inf"):
            return " no path to "
        if parent[i][j] == i:
            return " "
        else :
            return obtainPath(i, parent[i][j]) + str(parent[i][j]) + obtainPath(parent[i][j], j)


    for i in range (0,v):
        for j in range (0,v):
            if i == 0 and j == 0:
                print ("From :", i)
                print (" To :", j)
                print ("Path :" +  str(i) + obtainPath(i,j) + str(j))
                print ("Distance :", p[i][j])
                print("\n")
                
    #print(pd.DataFrame(p))
    return p
                
FloydWarshall(distances, [0,2,11,6,0])



From : 0
 To : 0
Path :0 16 7 3 0
Distance : 158.0




array([[1.58e+02, 3.40e+01, 8.50e+01, ..., 1.00e+11, 1.60e+01, 1.00e+11],
       [1.34e+02, 1.68e+02, 6.10e+01, ..., 1.00e+11, 1.50e+02, 1.00e+11],
       [7.70e+01, 1.11e+02, 1.62e+02, ..., 1.00e+11, 9.30e+01, 1.00e+11],
       ...,
       [1.00e+11, 1.00e+11, 1.00e+11, ..., 1.00e+11, 1.00e+11, 1.00e+11],
       [1.42e+02, 1.76e+02, 6.90e+01, ..., 1.00e+11, 1.58e+02, 1.00e+11],
       [1.00e+11, 1.00e+11, 1.00e+11, ..., 1.00e+11, 1.00e+11, 1.00e+11]])

## Main function

In [24]:
## Data structures
set_seed()
distances = distances
# To stop algorithm
import timeit

# Time setting
inicio = timeit.default_timer()
fim = timeit.default_timer() - 15
time = fim - inicio
#print(inicio,fim,time)

iterations = 0
grand_iterations = 0

## ILS
ils_parameter = 3
min_total_distance = 1000000
routes = []

while(time < 2): # 2 seconds max
    ## Create initial solution
    # routes_initial = createInitialSolutionRandomly(nVehicles, nGroups)
    routes_initial, demand_distribution = createInitialSolutionByBruteForce(nVehicles, nGroups, capacity, demands)
    #print('initial routes : ', routes_initial)

    distancesPerVehicle = calculateDistancesForRoutes(routes_initial, distances)
    routes, distancesPerRoute = localSearch(routes_initial, distancesPerVehicle)
    total_distance = sum(distancesPerRoute)

    # Applying ils_parameter perturbations
    for i in range(ils_parameter): 
        perturbated_routes = perturbate(routes_iteration)
        new_routes = localSearch(perturbated_routes)
        new_distance = calculateDistance(new_routes, distances)
        if new_distance < min_total_distance_iteration:
            min_total_distance_iteration = new_distance
            routes_iteration = new_routes
        iterations += 1
    # Checking if the solution of this iteration is better than the global solution
    if min_total_distance_iteration < min_total_distance:
        min_total_distance = min_total_distance_iteration
        routes = routes_iteration
    grand_iterations += 1 

    fim = timeit.default_timer()
    time = fim - inicio

print('number of grand iterations and iterations in 2 seconds : ', grand_iterations, iterations)
print(routes)
print(demand_distribution)
print(calculateDistance(routes, distances))



From : 0
 To : 0
Path :0 28 26 10 21 14 23 15 22 0
Distance : 637.0




From : 0
 To : 0
Path :0 20 6 0
Distance : 150.0


hola
[0, 1, 2, 3, 4, 5, 6, 7, 8, 0]
iterations :  0
6
[1, 2, 3, 4, 5, 7, 8]
[0, 1, 2, 3, 4, 5, 6, 7, 8, 0] 6 5
[0, 1, 2, 3, 4, 5, 6, 7, 8, 0] 6 5
saindo
iterations :  0
6
[1, 2, 3, 4, 5, 7, 8, 9, 10]
[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0] 6 7
[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0] 6 9
iterations :  1
6
[1, 2, 3, 4, 5, 7, 8, 9, 10]
[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0] 6 2
[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0] 6 2
iterations :  2
10
[1, 2, 3, 4, 5, 6, 7, 8, 9]
[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0] 8 2
[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0] 10 2
iterations :  3
3
[1, 2, 4, 5, 6, 7, 8, 9, 10]
[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0] 3 6
[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0] 3 6
iterations :  4
8
[1, 2, 3, 4, 5, 6, 7, 9, 10]
[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0] 6 6
[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0] 8 6
iterations :  5
4
[1, 2, 3, 5, 6, 7, 8, 9, 10]
[0, 1, 2, 3, 4, 5, 6, 5, 6, 7

[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5

[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5

[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5

[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5

...

[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5

[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5

[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5

[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8, 0], [0, 9, 10, 9, 10, 0]]
[[0, 1, 2, 3, 4, 5, 6, 5

KeyboardInterrupt: 

## Plot

In [ ]:
import networkx as nx
G = nx.DiGraph()

node = 1
#labels = {}
nodecolors = []
count_nodes = 0
for node in nodes:
    pos = [node[0],node[1]]
    G.add_node(count_nodes, pos = pos)
    G.node[count_nodes]['group'] = node[2]
    count_nodes+=1

# Mudar para pegar o elemento do grupo que é visitado POR GRUPO
for vehicleRoute in routes:
    for i in range(len(vehicleRoute) - 1):
        G.add_edge(vehicleRoute[i], vehicleRoute[i+1])
        
colors = ['cadetblue','red','blue','green','yellow', 'darkgreen', 'mediumpurple', 'purple', 'grey', 'greenyellow', 'pink', 'lightblue']
pos=nx.get_node_attributes(G,'pos')
#print(pos)
nx.draw(G, pos, with_labels = True)
for i in range(0,len(colors)):
    nodelist = []
    for node in G.nodes():
        #print(node)
        if G.node[node]['group'] == i:
            nodelist.append(node)
    nx.draw_networkx_nodes(G, pos=pos, nodelist=nodelist, node_size=400, node_color=colors[i], with_labels = True)
    #print(nodelist)
    i+=1